<a href="https://www.kaggle.com/code/sofiamatias/learning-equality-challenge-semanticsearch?scriptVersionId=121684956" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

# Imports

In [1]:
import sys, os
sys.path.append("../input/sentence-transformer-package/sentence-transformers-2.2.2/sentence-transformers-2.2.2") 
import sentence_transformers
from sentence_transformers import SentenceTransformer, CrossEncoder, util

In [2]:
import numpy as np
import pandas as pd
import string
import torch

# Loading dataframes

In [3]:
challenge_files_path = '/kaggle/input/learning-equality-curriculum-recommendations'
private_files_path = '/kaggle/input/learningequalityfiles'
model_files_path = '/kaggle/input/sentence-transformer-package'

print (f"\nLoading dataframes...")

for dirname, _, filenames in os.walk(challenge_files_path):
    for filename in filenames:
        filepath = os.path.join(dirname, filename)
        print (f"\nLoading dataframe from {filepath}...")
        df = pd.read_csv (filepath)
        if 'topics' in filepath:
            topics_df = df.fillna({"title": "", "description": ""})
            display(topics_df)
        elif 'sample_submission' in filepath:
            print (f"\nLoading 'sample' dataframe...")
            sample_df = df
            display(sample_df)
        elif 'correlations' in filepath:
            correlations_df = df.fillna({"title": "", "description": ""})
            display(correlations_df)
            print (f"\nCreating exploded correlations 'corr' dataframe")
            corr_df = correlations_df.copy()
            corr_df['content_ids'] = corr_df.content_ids.str.split(' ')
            corr_df = corr_df.explode('content_ids')
            display (corr_df)
        elif 'content' in filepath:
            contents_df = df.fillna({"title": "", "description": "", "text": ""})
            display(contents_df)
print (f"\nDataframes loaded.")


Loading dataframes...

Loading dataframe from /kaggle/input/learning-equality-curriculum-recommendations/sample_submission.csv...

Loading 'sample' dataframe...


topic_id                                        content_ids
0  t_00004da3a1b2  c_1108dd0c7a5d c_376c5a8eb028 c_5bc0e1e2cba0 c...
1  t_00068291e9a4  c_639ea2ef9c95 c_89ce9367be10 c_ac1672cdcd2c c...
2  t_00069b63a70a                                     c_11a1dc0bfb99
3  t_0006d41a73a8  c_0c6473c3480d c_1c57a1316568 c_5e375cf14c47 c...
4  t_4054df11a74e                      c_3695c5dc1df6 c_f2d184a98231


Loading dataframe from /kaggle/input/learning-equality-curriculum-recommendations/topics.csv...


id                                              title  \
0      t_00004da3a1b2                         Откриването на резисторите   
1      t_000095e03056             Unit 3.3 Enlargements and Similarities   
2      t_00068291e9a4                    Entradas e saídas de uma função   
3      t_00069b63a70a                                        Transcripts   
4      t_0006d41a73a8  Графики на експоненциални функции (Алгебра 2 н...   
...               ...                                                ...   
76967  t_fffb0bf2801d                             4.3 Graph of functions   
76968  t_fffbe1d5d43c                   Inscribed shapes problem solving   
76969  t_fffe14f1be1e                                          Lección 7   
76970  t_fffe811a6da9  تحديد العلاقة بين الإحداثيّات القطبية والإحداث...   
76971  t_fffe88835149  Formation of shadows and eclipses (umbra and p...   

                                             description channel category  \
0      Изследване на материали, които предизвикват на...  000cf7   source   
1                                                         b3f329  aligned   
2                   Entenda um pouco mais sobre funções.  8e286a   source   
3                                                         6e3ba4   source   
4      Научи повече за графиките на сложните показате...  000cf7   source   
...                                                  ...     ...      ...   
76967                                                     e77b55  aligned   
76968  Use properties of inscribed angles to prove pr...  0c929f   source   
76969                                                     6e90a7  aligned   
76970                           5b9e5ca86571f90499ea987f  9fd860   source   
76971                                                     c7ca13  aligned   

       level language          parent  has_content  
0          4       bg  t_16e29365b50d         True  
1          2       en  t_aa32fb6252dc        False  
2          4       pt  t_d14b6c2a2b70         True  
3          3       en  t_4054df11a74e         True  
4          4       bg  t_e2452e21d252         True  
...      ...      ...             ...          ...  
76967      4       en  t_676e6a1a4dc7        False  
76968      4       sw  t_50145b9bab3f         True  
76969      6       es  t_d448c707984d         True  
76970      2       ar  t_5b4f3ba4eb7d         True  
76971      4       en  t_988923176459        False  

[76972 rows x 9 columns]


Loading dataframe from /kaggle/input/learning-equality-curriculum-recommendations/correlations.csv...


...


Creating exploded correlations 'corr' dataframe


topic_id     content_ids
0      t_00004da3a1b2  c_1108dd0c7a5d
0      t_00004da3a1b2  c_376c5a8eb028
0      t_00004da3a1b2  c_5bc0e1e2cba0
0      t_00004da3a1b2  c_76231f9d0b5e
1      t_00068291e9a4  c_639ea2ef9c95
...               ...             ...
61513  t_fff9e5407d13  c_d64037a72376
61514  t_fffbe1d5d43c  c_46f852a49c08
61514  t_fffbe1d5d43c  c_6659207b25d5
61515  t_fffe14f1be1e  c_cece166bad6a
61516  t_fffe811a6da9  c_92b8fad372ee

[279919 rows x 2 columns]


Loading dataframe from /kaggle/input/learning-equality-curriculum-recommendations/content.csv...


id                                             title  \
0       c_00002381196d  Sumar números de varios dígitos: 48,029+233,930    
1       c_000087304a9e                    Trovare i fattori di un numero   
2       c_0000ad142ddb                           Sumar curvas de demanda   
3       c_0000c03adc8d                               Nado de aproximação   
4       c_00016694ea2a                  geometry-m3-topic-a-overview.pdf   
...                ...                                               ...   
154042  c_fffcbdd4de8b                                  2. 12: Diffusion   
154043  c_fffe15a2d069                      Sommare facendo gruppi da 10   
154044  c_fffed7b0d13a                            Introdução à subtração   
154045  c_ffff04ba7ac7                                      SA of a Cone   
154046  c_ffffe5254266                                          The Jats   

                                              description      kind  \
0       Suma 48,029+233,930 mediante el algoritmo está...     video   
1                         Sal trova i fattori di 120.\n\n     video   
2                       Cómo añadir curvas de demanda\n\n     video   
3       Neste vídeo você vai aprender o nado de aproxi...  document   
4                        geometry-m3-topic-a-overview.pdf  document   
...                                                   ...       ...   
154042                                                        html5   
154043  Sal somma 5+68 spezzando il 5 in un 2 e un 3.\n\n     video   
154044  Sal fala sobre o que significa subtrair. Os ex...     video   
154045                                                        video   
154046                                                        video   

                                                     text language  \
0                                                               es   
1                                                               it   
2                                                               es   
3       \nNado de aproximação\nSaber nadar nas ondas ...       pt   
4       Estándares Comunes del Estado de Nueva York\n\...       es   
...                                                   ...      ...   
154042  What will eventually happen to these dyes?\n\n...       en   
154043                                                          it   
154044                                                          pt   
154045                                                          en   
154046                                                          en   

        copyright_holder      license  
0                    NaN          NaN  
1                    NaN          NaN  
2                    NaN          NaN  
3       Sikana Education  CC BY-NC-ND  
4              Engage NY  CC BY-NC-SA  
...                  ...          ...  
154042    CSU and Merlot  CC BY-NC-SA  
154043               NaN          NaN  
154044               NaN          NaN  
154045               NaN          NaN  
154046               NaN          NaN  

[154047 rows x 8 columns]


Dataframes loaded.


# Choosing sample data

In [4]:
print ("\nDefining sampled dataset...")
use_submission_sample = False
samples = 1000
if ~sample_df.empty and use_submission_sample:
    corr_df = corr_df[corr_df.topic_id.isin(sample_df.topic_id)]
    correlations_df = correlations_df[correlations_df.topic_id.isin(sample_df.topic_id)]
    topics_df = topics_df[topics_df.id.isin(sample_df.topic_id)]
    samples = 5
    print (f"\nFiltered 'topics' to {len(topics_df)} samples and 'contents' to {len(contents_df)} samples")
else:
    topics_df = topics_df[topics_df.has_content == True].sample(n=samples)
    corr_df = corr_df[corr_df.topic_id.isin(topics_df.id)]
    correlations_df = correlations_df[correlations_df.topic_id.isin(topics_df.id)]

display (topics_df)
display (contents_df)
display (correlations_df)


Defining sampled dataset...


id                                              title  \
19860  t_42cbc803cf94                                       নিজে করি (১)   
65967  t_dbf5bb94eb80                 Les propriétés des transformations   
43793  t_92c1843d7e59                                 NM_U09 - Narrative   
9164   t_1ef4e6ff96f8                                        Water Cycle   
32116  t_6b32374f9955                                      Question Tags   
...               ...                                                ...   
35489  t_767a072eed16                                 Comparar decimales   
55570  t_b9e26ec8aa6d                 Trecho D9: Computadores E Internet   
2896   t_09c10716e41f  Mixed Addition and Subtraction in Compound Uni...   
27650  t_5c9119f2259f               Unknown Dimensions of Parallelograms   
59073  t_c53f190c7263               Introduction to systems of equations   

                                             description channel  \
19860                                                     00a2b4   
65967                     Les propriétés des isométries.  c152d6   
43793                                                     bae253   
9164                                                      ef2088   
32116                                                     b4897d   
...                                                  ...     ...   
35489  ¡Vamos a probar nuestro conocimiento sobre dec...  484bd2   
55570  (EF07CI06) Discutir e avaliar mudanças econômi...  57e9d3   
2896                                                      fef095   
27650                                                     fef095   
59073  Learn what "systems of equations" are, what co...  0ec697   

           category  level language          parent  has_content  
19860       aligned      4       bn  t_3176bf99157e         True  
65967        source      4       fr  t_5bff38be3df5         True  
43793  supplemental      2       en  t_9b065be88adb         True  
9164   supplemental      5       en  t_8accfb2ecc67         True  
32116  supplemental      4       en  t_6793f6ce3deb         True  
...             ...    ...      ...             ...          ...  
35489  supplemental      4       es  t_56a7de936c2d         True  
55570       aligned      5       pt  t_dfb6a10f183c         True  
2896         source      6       en  t_f25847e1ebb7         True  
27650        source      4       en  t_3e216e4c3233         True  
59073        source      5       en  t_0a76a18d2d3c         True  

[1000 rows x 9 columns]

id                                             title  \
0       c_00002381196d  Sumar números de varios dígitos: 48,029+233,930    
1       c_000087304a9e                    Trovare i fattori di un numero   
2       c_0000ad142ddb                           Sumar curvas de demanda   
3       c_0000c03adc8d                               Nado de aproximação   
4       c_00016694ea2a                  geometry-m3-topic-a-overview.pdf   
...                ...                                               ...   
154042  c_fffcbdd4de8b                                  2. 12: Diffusion   
154043  c_fffe15a2d069                      Sommare facendo gruppi da 10   
154044  c_fffed7b0d13a                            Introdução à subtração   
154045  c_ffff04ba7ac7                                      SA of a Cone   
154046  c_ffffe5254266                                          The Jats   

                                              description      kind  \
0       Suma 48,029+233,930 mediante el algoritmo está...     video   
1                         Sal trova i fattori di 120.\n\n     video   
2                       Cómo añadir curvas de demanda\n\n     video   
3       Neste vídeo você vai aprender o nado de aproxi...  document   
4                        geometry-m3-topic-a-overview.pdf  document   
...                                                   ...       ...   
154042                                                        html5   
154043  Sal somma 5+68 spezzando il 5 in un 2 e un 3.\n\n     video   
154044  Sal fala sobre o que significa subtrair. Os ex...     video   
154045                                                        video   
154046                                                        video   

                                                     text language  \
0                                                               es   
1                                                               it   
2                                                               es   
3       \nNado de aproximação\nSaber nadar nas ondas ...       pt   
4       Estándares Comunes del Estado de Nueva York\n\...       es   
...                                                   ...      ...   
154042  What will eventually happen to these dyes?\n\n...       en   
154043                                                          it   
154044                                                          pt   
154045                                                          en   
154046                                                          en   

        copyright_holder      license  
0                    NaN          NaN  
1                    NaN          NaN  
2                    NaN          NaN  
3       Sikana Education  CC BY-NC-ND  
4              Engage NY  CC BY-NC-SA  
...                  ...          ...  
154042    CSU and Merlot  CC BY-NC-SA  
154043               NaN          NaN  
154044               NaN          NaN  
154045               NaN          NaN  
154046               NaN          NaN  

[154047 rows x 8 columns]

topic_id                                        content_ids
205    t_00f10f4588ea  c_312fb79e3dee c_4faa6187f8fa c_718d9f96b878 c...
223    t_0108e02a3be7                                     c_1e91e0b25cda
237    t_01117610b649  c_38786dc5f424 c_4895251051e2 c_55cd11fc6b3d c...
323    t_01774d29b58e  c_055aa637cd5e c_0655115498c3 c_0aec8d9ab8f3 c...
349    t_0194fc455712       c_834fc0e8eac1 c_84783cdeebdf c_adaadf13ff78
...               ...                                                ...
61037  t_fe21e3004c83  c_0dff7598a60b c_1b55268a53c8 c_7850af38ad42 c...
61060  t_fe3f90bfdb94  c_08f8d103a84f c_2caa59f592f0 c_40579c306c94 c...
61201  t_febf45b693a3  c_44ccd51608eb c_532b8744553b c_5966e82236d3 c...
61292  t_ff16994b9084                      c_0d405e8e1e75 c_36d61acd8441
61307  t_ff24a29b656c                      c_309f5bf6e8e3 c_92390344e985

[1000 rows x 2 columns]

# Cleaning data

* Remove ponctuation and special chars from text fields
* Delete columns 'copyright_holder' and 'license' from 'contents'
* Filter 'topics' by 'has_content' = True
* Group 'topics' and 'contents' by language
* Change 'level' column from numbers to text

In [5]:
def clean_text(text_col):
    """
    Clean ponctuation and special chars from a dataframe column
    """
    punctuations = string.punctuation
    text_col = text_col.str.replace('\W', ' ', regex=True)
    for punct in string.punctuation:
        text_col = text_col.str.replace(punct, ' ', regex=True)
    return text_col.str.lower()

In [6]:
# Cleaning topics
levels = {1: 'Level 1', 2: 'Level 2', 3: 'Level 3', 4: 'Level 4', 5: 'Level 5', 6: 'Level 6', 7: 'Level 7', 
          8: 'Level 8', 9: 'Level 9', 10: 'Level 10', 0: 'Level 0'}
topics_cols = ['title', 'description']

print (f"\nCreating and cleaning topic features...")
topic_features = topics_df.copy()
topic_features = topic_features.replace ({'level': levels})
for col in topics_cols:
    topic_features[col] = clean_text(topic_features[col])
topic_features.sort_values (by='language', inplace=True)

#topics_features['sentences'] = topics_features[topics_cols].apply(lambda x: '.'.join(x.dropna().astype(str)), axis=1)
#topics_features = topics_features.drop(columns=['parent'] + topics_cols) 
print (f"\nCreated 'topic_features'")
display (topic_features)


Creating and cleaning topic features...

Created 'topic_features'


id                                              title  \
15647  t_3463678f5471  يتعرف النسب المثلثية  جا  جتا  ظا   للزوايا وت...   
12060  t_287f118719de  مثال عملي لإنشاء كلاس الكتاب   الجزء الثاني  عملي   
44033  t_93815f4d6066   مثال عملي لإنشاء كلاس الكتاب   الجزء الأول  عملي   
33618  t_7047335ea50b  يتعرف الأعداد غير النسبي ة   يمي ز بين العدد ا...   
705    t_026969b7c3f1                                    فاح ت   خ زامى    
...               ...                                                ...   
28806  t_60680372e6e2                                               关系代词   
67062  t_df6ecedabb6b                                               简单图案   
59024  t_c515726fe28d                                               拦网练习   
70438  t_ea74c676f613                                               相等比值   
48093  t_a0ea2d645955                                            含变量的分配律   

                                             description channel category  \
15647                                                     5139e9   source   
12060                                                     5139e9   source   
44033                                                     5139e9   source   
33618                           5add9f098f9c1404a0d15b8e  9fd860   source   
705                                                       7b47c5   source   
...                                                  ...     ...      ...   
28806                                                     f83dcf   source   
67062                                                     da1fa7   source   
59024                                                     da1fa7   source   
70438                                                     f83dcf   source   
48093  学习如何将分配属性应用到数值表达式中 不含变量  和代数表达式中 含变量  分配属性有时也被...  f83dcf   source   

         level language          parent  has_content  
15647  Level 6       ar  t_a753bc8b4f91         True  
12060  Level 5       ar  t_344131c2889b         True  
44033  Level 5       ar  t_344131c2889b         True  
33618  Level 3       ar  t_2c789471322c         True  
705    Level 4       ar  t_3a7d8912b3bf         True  
...        ...      ...             ...          ...  
28806  Level 4       zh  t_6ae20a3a8ffc         True  
67062  Level 3       zh  t_73ea7d95464d         True  
59024  Level 3       zh  t_52ef71cb2010         True  
70438  Level 4       zh  t_8db8667d3008         True  
48093  Level 4       zh  t_71ee98789a46         True  

[1000 rows x 9 columns]

In [7]:
# Cleaning contents
content_cols = ['title']


print (f"\nCreating and cleaning content features...")
content_features = contents_df.copy()
for col in content_cols:
    content_features[col] = clean_text(content_features[col])
#content_features['sentences'] =  content_features[content_cols].apply(lambda x: '.'.join(x.dropna().astype(str)), axis=1)
content_features.sort_values (by='language', inplace=True)
content_features.drop(columns=['copyright_holder', 'license'], inplace=True)
print (f"\nCreated 'content_features'")
display(content_features)


Creating and cleaning content features...

Created 'content_features'


id                                              title  \
133868  c_de43cff8dd60                                 المفردات والتراكيب   
63589   c_699d4bd5d5bb                                 المفردات والتراكيب   
17214   c_1cab88377df5                                 المفردات والتراكيب   
145550  c_f1b8123b975e                                          الس  ف ر    
17202   c_1ca6079deb47  يعي ن معكوس مصفوفة مرب عة من الرتبة الثالثة با...   
...                ...                                                ...   
15012   c_18fc5ad44e5d                                          构建比较级和最高级   
128758  c_d5e56175090a                                             主谓一致简介   
32558   c_35f7982b250f                                          双臂和胯部热身运动   
15053   c_19148c5d7ab3                                                 出血   
117915  c_c3b030650102                                              踩单车动作   

                                              description      kind  \
133868                                                     exercise   
63589                                                      exercise   
17214                                                      exercise   
145550  يركب "رامي" الطّائرة للمرّة الأولى فيحقّق أمله...     html5   
17202                            5ad46b8a6b9064043d8b4158  exercise   
...                                                   ...       ...   
15012                                学习如何改装比较级和最高级修饰语\n\n     video   
128758                 主谓一致指匹配一个句子的主语和动词！这里介绍它是怎么一回事.\n\n     video   
32558             在本视频中，您将学会三个热身练习，锻炼您上半身的肌肉，尤其是双臂和胯部的肌肉。  document   
15053   微博：http://www.weibo.com/sikana\r\n脸书：https://w...  document   
117915                         本视频面向初学者，教给您如何完成足球中的踩单车动作。     video   

                                                     text language  
133868  ما المقصود بعبارة: "هل هناك من خطب"؟\n\n- هل ه...       ar  
63589   ما ضدّ "لا تملّ" في الجملة الآتية: "تُعيدُ الأ...       ar  
17214   ما مرادف "يتمّم" في ما يلي: "يَقِفُ أَحْيانًا ...       ar  
145550  السَّفَرُ\n\nبِحِرْصٍ شَديدٍ، حَزَمَ "رامي" أَ...       ar  
17202   ![](${☣ CONTENTSTORAGE}/40cf62978d6581e03a5085...       ar  
...                                                   ...      ...  
15012                                                           zh  
128758                                                          zh  
32558   \n双臂和胯部热身运动\n双臂和胯部热身运动\n在本视频中，您将学会三个热身练习，锻炼您上...       zh  
15053   \n出血\n本视频由红十字会和Sikana共同出品\n急救\n出血\n在这个视频您将学习怎...       zh  
117915                                                          zh  

[154047 rows x 6 columns]

# Scoring: F2 score 

In [8]:
def calculate_F2score(pred_df, act_df):
    
    """
    Using predictions_df and actual_df as exploded correlation columns to calculate F1 score.
    Results show correct predicts, recall, precision and F2 score.
    Results also return the list of correct predicts, correct_df_
    """
    print ('\nCalculating scores...')
    if pred_df.empty or act_df.empty:
        print ('\nOne or both dataframes are empty. Abort F2score calculation.')
        return None
    prediction_df=pred_df.copy()
    actual_df = act_df.copy()
    prediction_df.columns=['topic_id', 'content_ids_pred']
    actual_df.columns=['topic_id', 'content_ids_actual']
    df = pd.merge(prediction_df, actual_df, how='inner', on='topic_id')
    if df.empty:
        print ('\nNo matches between predictions and correlations. Abort F2score calculation.')
        return None
    df['tp'] = df[['content_ids_pred', 'content_ids_actual']].apply (lambda x: len(set(x['content_ids_actual'].split()).intersection(set(x['content_ids_pred'].split()))), axis=1)
    df['fp'] = df[['content_ids_pred', 'content_ids_actual']].apply (lambda x: len(set(x['content_ids_pred'].split()) - set(x['content_ids_actual'].split())), axis=1)
    df['fn'] = df[['content_ids_pred', 'content_ids_actual']].apply (lambda x: len(set(x['content_ids_actual'].split()) - set(x['content_ids_pred'].split())), axis=1)
    df['precision'] = df['tp'] / (df['tp'] + df['fp'])
    df['recall'] = df['tp'] / (df['tp'] + df['fn'])
    df['f2'] = df['tp'] / (df['tp'] + 0.2 * df['fp'] + 0.8 * df['fn']) 
    print ('\nF2 score calculation finished.')

    return df

# Getting matches: sentence transformer with retrain-rerank

In [9]:
def search(query, topic_embedding, corpus_embeddings, content_sentences, content_ids, cross_encoder, top_k):

    # passages = content_sentences

    ##### Semantic Search #####
    # find potentially relevant passages
    hits = util.semantic_search(topic_embedding, corpus_embeddings, top_k=50)
    hits = hits[0]  # Get the hits for the first query

    ##### Re-Ranking #####
    # Now, score all retrieved passages with the cross_encoder
    cross_inp = [[query, content_sentences[hit['corpus_id']]] for hit in hits]
    cross_scores = cross_encoder.predict(cross_inp)

    # Sort results by the cross-encoder scores
    for idx in range(len(cross_scores)):
        hits[idx]['cross-score'] = cross_scores[idx]

    # Output of top-30 hits from re-ranker
    hits = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
    results = {}
    for hit in hits[0:top_k]:
        results[content_ids.iloc[hit['corpus_id']]] = content_sentences[hit['corpus_id']]
    return results

In [10]:
from tqdm import tqdm

gpu_on = True

if not torch.cuda.is_available():
    print("Warning: No GPU found. Please add GPU to your notebook")
    gpu_on = False
    
languages = topic_features.language.unique()
print (languages)
preds = {}
matches = {}
biencoder = "/kaggle/input/learning-equality-st-train-sm/ST-all-MiniLM-L6-v2-trained"
crossencoder = '/kaggle/input/msmarcominilml6v2/ms-marco-MiniLM-L-6-v2'

print (f"\nGetting matches using bi-encoder {biencoder} and cross encoder {crossencoder}...")

#Use the Bi-Encoder to encode all contents, so that we can use it with semantic search
bi_encoder = SentenceTransformer(biencoder)
bi_encoder.max_seq_length = 256    #Truncate long passages to 256 tokens (256 is ideal value)
top_k = 5                         #Number of passages we want to retrieve with the bi-encoder (10 is ideal value)

#Use a cross-encoder, to re-rank the results list to improve the quality
cross_encoder = CrossEncoder(crossencoder)

for lang in languages:
    print ('\nWorking on topics for language ', lang)
    content_sentences = content_features[content_features.language == lang]
    topic_sentences = topic_features[topic_features.language == lang]

    if len(content_sentences) == 0:
        print ('\nNo contents for this language.')
        continue
    if len(topic_sentences) == 0:
        print ('\nNo topics for this language.')
        continue

    
    print ("\nCalculating 'content' embeddings...")

    # encode all contents into our vector space. This takes about 5 minutes (depends on your GPU speed)
    corpus_embeddings = bi_encoder.encode(content_sentences.title.to_list(), convert_to_tensor=True, show_progress_bar=True)
    
    if gpu_on:
        corpus_embeddings = corpus_embeddings.cuda()
        corpus_embeddings = util.normalize_embeddings(corpus_embeddings)
    
    print ("\nCalculating 'topic' embeddings...")
    
    # Encode the topics using the bi-encoder
    topic_embeddings = bi_encoder.encode(topic_sentences.title.to_list(), convert_to_tensor=True, show_progress_bar=False)
    
    if gpu_on:
        topic_embeddings = topic_embeddings.cuda()
        topic_embeddings = util.normalize_embeddings(topic_embeddings)
    
    print ("\nRunning matches...")
    
    for i, (topic_embed, query) in enumerate(tqdm(zip (topic_embeddings, topic_sentences.title.to_list()), total=len(topic_sentences))):
        results = search(query,
                         topic_embed,
                         corpus_embeddings, 
                         content_sentences.title.to_list(), 
                         content_sentences.id,
                         cross_encoder,
                         top_k)
        matches[query] = results.values()
        preds[topic_sentences.iloc[i].id] = results.keys()
print ('\nEnd of calculating matches.')

['ar' 'as' 'bg' 'bn' 'en' 'es' 'fil' 'fr' 'gu' 'hi' 'it' 'km' 'kn' 'mr'
 'my' 'or' 'pl' 'pt' 'ru' 'sw' 'swa' 'zh']

Getting matches using bi-encoder /kaggle/input/learning-equality-st-train-sm/ST-all-MiniLM-L6-v2-trained and cross encoder /kaggle/input/msmarcominilml6v2/ms-marco-MiniLM-L-6-v2...

Working on topics for language  ar

Calculating 'content' embeddings...


Batches:   0%|          | 0/232 [00:00<?, ?it/s]


Calculating 'topic' embeddings...

Running matches...


  0%|          | 0/63 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

 90%|█████████ | 9/10 [00:02<00:00,  5.03it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

100%|██████████| 10/10 [00:02<00:00,  4.37it/s]


End of calculating matches.


In [11]:
# predictions in exploded format
preds_df = pd.DataFrame(zip (list(preds.keys()), [list(vals) for vals in preds.values()]), columns=['id','content_ids']).explode('content_ids')

# predictions in submissions format
df_preds_aux = pd.DataFrame(zip (list(preds.keys()), (' '.join(list(preds[key])) for key in preds.keys())), columns=['id','content_ids'])

predicts_submission = pd.DataFrame(topics_df.id).merge (df_preds_aux, how ='left', on = 'id')
predicts_submission.rename(columns={'id':'topic_id'}, inplace=True)
predicts_submission.fillna(' ', inplace=True)

predicts_submission
#predicts_submission.content_ids.apply (lambda x: len(x.split()))

topic_id                                        content_ids
0    t_42cbc803cf94  c_e3f7f29e3f5f c_167b12c23824 c_25c11355e7ce c...
1    t_dbf5bb94eb80  c_a52c8d50da07 c_21870324ebe0 c_4fe00ca53d1e c...
2    t_92c1843d7e59  c_4cb826fab827 c_b271cfe1ca48 c_29ed03438232 c...
3    t_1ef4e6ff96f8  c_bca191142293 c_7b2f1f26f4a7 c_331717624d43 c...
4    t_6b32374f9955  c_0fa0b4d4a397 c_35e4956629c1 c_ee220680bb42 c...
..              ...                                                ...
995  t_767a072eed16  c_455e1e36e13c c_0d6d47776ece c_93198bc4f026 c...
996  t_b9e26ec8aa6d  c_09c07434634a c_5bb61755f9a4 c_b93af84acdca c...
997  t_09c10716e41f  c_5822f6958d74 c_647822b81ebe c_ef9867ed30fc c...
998  t_5c9119f2259f  c_fb03b9a82cf8 c_24de7dd43edc c_63af0b6c602b c...
999  t_c53f190c7263  c_184a1c479c36 c_8ae68656b50d c_1317343b1a59 c...

[1000 rows x 2 columns]

# Model evaluation

In [12]:
scoring = True
if scoring:
    score = calculate_F2score(predicts_submission.sort_values('topic_id'), correlations_df)
    if score is not None:
        print(score)
        print ('F2 mean score:', score.f2.mean())
        print ('Correct predictions:', score.tp.sum())
        print ('Topics to match:', len(topics_df))
        print ('False positives:', score.fp.sum())
        print ('False negatives:', score.fn.sum())
        print ('Contents to match:', len(corr_df.merge (topics_df.id, how = 'inner', left_on='topic_id', right_on='id')))


Calculating scores...

F2 score calculation finished.
           topic_id                                   content_ids_pred  \
0    t_00f10f4588ea  c_c11aee9d9333 c_4faa6187f8fa c_890a97cf3c7a c...   
1    t_0108e02a3be7  c_2cda3b50fea6 c_ce588a79a056 c_1ff454e1bfd2 c...   
2    t_01117610b649  c_f6e2699acce2 c_242ffa6be81a c_9cdc0ea537c0 c...   
3    t_01774d29b58e  c_998127dd53c3 c_055aa637cd5e c_3a635b3e7b1a c...   
4    t_0194fc455712  c_84783cdeebdf c_9bd6069da782 c_55f7332af22a c...   
..              ...                                                ...   
995  t_fe21e3004c83  c_948008fd039b c_05c5e7f0f63c c_a09aa51e94bd c...   
996  t_fe3f90bfdb94  c_a97ad21325fd c_4810824f78ce c_dcae9f9ebae1 c...   
997  t_febf45b693a3  c_f6290c36c300 c_532b8744553b c_5b4e9a2921df c...   
998  t_ff16994b9084  c_70bc333bea66 c_36d61acd8441 c_7e0eb0a52cbc c...   
999  t_ff24a29b656c  c_28576ff51bff c_cd7114127e2f c_b464d0c13e50 c...   

                                    content_ids_actual  

# Submissions

In [13]:
#predicts_submission.to_csv('submission.csv', index=False)

# Cleaning wrong matches with LGBM

In [14]:
clean_wrong_matches = False

## Calculating features 'X_test' for predictions

In [15]:
def categorize_features (X: pd.DataFrame):
    obj_feat = list(X.loc[:, X.dtypes == 'object'].columns.values)
    for feature in obj_feat:
        X[feature] = pd.Series(X[feature], dtype="category")
    return X
    
def get_y_class (y):
    return (y > 0.5).astype("bool")

In [16]:
if clean_wrong_matches:
    X_test = preds_df.merge (topic_features, how='inner', on='id')
    X_test.drop (columns = ['language', 'has_content', 'description'], inplace=True)
    X_test.rename (columns = {'id': 'topic_id', 'title':'topic_title'}, inplace=True)
    X_test = X_test.merge (content_features, how='inner', left_on='content_ids', right_on='id')
    X_test.drop (columns = ['title', 'description', 'text', 'id'], inplace=True)
    X_test = categorize_features (X_test)
    display (X_test, X_test.dtypes)

In [17]:
#corr_df
#preds_df = preds_df.merge (corr_df, how='left', on = 'content_ids')
#preds_df['match'] = (preds_df.id == preds_df.topic_id)
#preds_df

# Get model (load existing model or train model)

In [18]:
import lightgbm as lgb

if os.path.exists(private_files_path) and clean_wrong_matches:
    for dirname, _, filenames in os.walk(private_files_path):
        for filename in filenames:
            filepath = os.path.join(dirname, filename)
    model = lgb.Booster(model_file=filepath)
    print ('Loaded model from :', filepath)
elif clean_wrong_matches:
    from sklearn.model_selection import train_test_split
    from sklearn.metrics import precision_score
    import lightgbm as lgb
    import optuna
    import datetime
        
    objective = 'binary'
    boosting_type = 'dart'

    def objective_lgbm(trial):
    
        param = {
            'boosting_type': boosting_type,
            'objective': objective,
            'is_unbalance': 'true',
            'metric': 'precision_score',
            'pos_bagging_fraction': trial.suggest_float('pos_bagging_fraction',0.1,1),
            'neg_bagging_fraction': trial.suggest_float('neg_bagging_fraction',0.1,1),
            'num_leaves': trial.suggest_int('num_leaves', 10,60),
            'max_depth': trial.suggest_int('max_depth', 10,60),
            'min_split_gain': trial.suggest_float('min_split_gain',0.1,1),
            'colsample_bytree': trial.suggest_float('colsample_bytree',0.1,1),
            'reg_alpha' : trial.suggest_float('reg_alpha',0.1,10),
            'reg_lambda': trial.suggest_float('reg_lambda',0.1,10),
            'n_estimators': trial.suggest_int('n_estimators', 150,350),
            'learning_rate': trial.suggest_float('learning_rate', 0.01,0.1),
            'verbosity': -1
        }
        num_boost_rounds = trial.suggest_int('num_boost_rounds', 50,400)
        model = lgb.train(param, train_data, num_boost_rounds)
        preds = model.predict(X_val)
        pred_labels = np.rint(preds)
        score = round(precision_score(y_val, pred_labels),4)
        return score
    
    # building a dataframe 'mix_matches' with 50% true topic-content matches and 50% false topic-content matches
    df_aux = preds_df.merge (corr_df, how='left', on='content_ids')
    true_matches = df_aux[df_aux['id'] == df_aux['topic_id']]
    true_matches_val = len(df_aux[df_aux['id'] == df_aux['topic_id']])
    false_matches = df_aux[df_aux['id'] != df_aux['topic_id']].sample(n=samples)
    mix_matches = pd.concat([true_matches, false_matches])
    mix_matches['y'] = (mix_matches.id == mix_matches.topic_id)
    mix_matches.drop (columns='topic_id', inplace=True)

    # building X features and y target 
    y = mix_matches['y']
    X = mix_matches.merge (topic_features, how='inner', on='id')
    #X = X.merge (content_features, how='inner', left_on='content_ids', right_on='id')
    X.drop (columns = ['language', 'has_content', 'description', 'y'], inplace=True)
    X.rename (columns = {'id': 'topic_id', 'title': 'topic_title'}, inplace=True)
    X = X.merge (content_features, how='inner', left_on='content_ids', right_on='id')
    X.drop (columns = ['title', 'description', 'text', 'id'], inplace=True)

    # preparing X and y for model: changing dtype to "category" and creating train/val sets
    X = categorize_features (X)

    print(f"Training features of shape {X.shape}")
    display (X)
    print(f"Training labels of shape {y.shape}")
    display (y)
    
    X_train, X_val, y_train, y_val = train_test_split (X, y, test_size = 0.3, random_state=42)

    train_data = lgb.Dataset(X_train, label = y_train)

    # get best hyperparameters
    study_lgbm = optuna.create_study(direction = 'maximize',study_name = "LGBM")
    study_lgbm.optimize(objective_lgbm, n_trials=50)

    trial_lgbm = study_lgbm.best_trial
    print("Model Accuracy --> ",trial_lgbm.value)
    print("Model's Best parameters --> ",trial_lgbm.params)

    # fit model and get score
    num_boost_rounds = trial_lgbm.params['num_boost_rounds']
    del trial_lgbm.params['num_boost_rounds']
    trial_lgbm.params['boosting_type'] = boosting_type
    trial_lgbm.params['objective'] = objective
    trial_lgbm.params['is_unbalance'] = True
    trial_lgbm.params['verbosity'] = -1
    print("Using parameters --> ",trial_lgbm.params)
    model = lgb.train(trial_lgbm.params, train_data, num_boost_rounds)
    pred_model = model.predict(X_val)
    pred_model = get_y_class (pred_model)
    score = precision_score(y_val, pred_model)
    print('\nLightGBM Model accuracy score: {0:0.4f}'.format(score))
    from sklearn.metrics import confusion_matrix
    print('\nConfusion Matrix : \n' + str(confusion_matrix(y_val,pred_model)))
    
    # save model
    date = datetime.datetime.now().strftime('%d%m%y-%H%M')
    model_filename = f"lgb-classifier-{date}.txt"
    model.save_model (model_filename)
    print ('\nSaved model as ', model_filename)

# New Predictions

In [19]:
if clean_wrong_matches:
    # get predictions
    preds_lgbm = model.predict(X_test)
    preds_lgbm = get_y_class (preds_lgbm)
    print ('\nPredictions: ', preds_lgbm[-50:])
    print (pd.DataFrame(preds_lgbm).value_counts())
    #put predictions in final format
    df_preds_aux = preds_df[preds_lgbm]
    print (df_preds_aux.groupby('id').count())
    df_preds_aux = df_preds_aux.groupby(['id']).apply (lambda x : ' '.join (x.iloc[:, 1])).reset_index()
    df_preds_aux.rename (columns = {0: 'content_ids'}, inplace=True)
    print (df_preds_aux)
    predicts_submission = pd.DataFrame(topics_df.id).merge (df_preds_aux, how ='left', on = 'id')
    predicts_submission.rename(columns={'id':'topic_id'}, inplace=True)
    predicts_submission.fillna(' ', inplace=True)

    display(predicts_submission)
    
    # submissions
    predicts_submission.to_csv('submission.csv', index=False)

In [20]:
predicts_submission.content_ids.apply (lambda x: len(x.split()))

0      5
1      5
2      5
3      5
4      5
      ..
995    5
996    5
997    5
998    5
999    5
Name: content_ids, Length: 1000, dtype: int64

# Final Score

In [21]:
if clean_wrong_matches and scoring:
    score = calculate_F2score(predicts_submission.sort_values('topic_id'), correlations_df)
    if score is not None:
        display(score)
        print ('F2 mean score:', score.f2.mean())
        print ('Correct predictions:', score.tp.sum())
        print ('Topics to match:', len(topics_df))
        print ('False positives:', score.fp.sum())
        print ('False negatives:', score.fn.sum())
        print ('Contents to match:', len(corr_df.merge (topics_df.id, how = 'inner', left_on='topic_id', right_on='id')))

In [22]:
predicts_submission.to_csv('submission.csv', index=False)